# california-coronavirus-data examples

By [Ben Welsh](https://palewi.re/who-is-ben-welsh)

A demonstration of how to use Python to work with the Los Angeles Times' independent tally of coronavirus cases in California published on GitHub at [datadesk/california-coronavirus-data](https://github.com/datadesk/california-coronavirus-data#state-cdph-totalscsv). To run this notebook immediately in the cloud,  click the [Binder](https://mybinder.org/) launcher below.

[![Binder](https://mybinder.org/badge_logo.svg)](https://mybinder.org/v2/gh/datadesk/california-coronavirus-data/master?urlpath=lab/tree/notebooks/examples.ipynb)

In [1]:
%load_ext lab_black

## Import Python tools

Our data analysis and plotting tools

In [2]:
import pandas as pd
import altair as alt

Customizations to the Altair theme

In [3]:
import altair_latimes as lat

In [4]:
alt.themes.register("latimes", lat.theme)
alt.themes.enable("latimes")

ThemeRegistry.enable('latimes')

In [5]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

## Import data

Read in the agency totals

In [6]:
agency_df = pd.read_csv("../latimes-agency-totals.csv", parse_dates=["date"])

In [7]:
agency_df.head()

agency   county  fips       date  confirmed_cases  deaths  recoveries  \
0   Alameda  Alameda     1 2020-06-21             4686   117.0         NaN   
1  Berkeley  Alameda     1 2020-06-21              119     1.0         NaN   
2    Alpine   Alpine     3 2020-06-21                1     0.0         1.0   
3    Amador   Amador     5 2020-06-21               13     0.0        10.0   
4     Butte    Butte     7 2020-06-21               94     1.0        72.0   

  did_not_update  
0            NaN  
1            NaN  
2           True  
3            NaN  
4           True

In [8]:
agency_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6293 entries, 0 to 6292
Data columns (total 8 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   agency           6293 non-null   object        
 1   county           6293 non-null   object        
 2   fips             6293 non-null   int64         
 3   date             6293 non-null   datetime64[ns]
 4   confirmed_cases  6293 non-null   int64         
 5   deaths           6292 non-null   float64       
 6   recoveries       2095 non-null   float64       
 7   did_not_update   893 non-null    object        
dtypes: datetime64[ns](1), float64(2), int64(2), object(3)
memory usage: 393.4+ KB


## Aggregate data

### By state

Lump all the agencies together and you get the statewide totals.

In [9]:
state_df = (
    agency_df.groupby(["date"])
    .agg({"confirmed_cases": "sum", "deaths": "sum"})
    .reset_index()
)

In [10]:
state_df.head()

date  confirmed_cases  deaths
0 2020-01-26                2     0.0
1 2020-01-27                3     0.0
2 2020-01-28                3     0.0
3 2020-01-29                4     0.0
4 2020-01-30                4     0.0

In [11]:
state_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 148 entries, 0 to 147
Data columns (total 3 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             148 non-null    datetime64[ns]
 1   confirmed_cases  148 non-null    int64         
 2   deaths           148 non-null    float64       
dtypes: datetime64[ns](1), float64(1), int64(1)
memory usage: 3.6 KB


### By county

Three cities &mdash; Berkeley, Long Beach and Pasadena &mdash; run independent public health departments. Calculating county-level totals requires grouping them with their local peers.

In [12]:
county_df = (
    agency_df.groupby(["date", "county"])
    .agg({"confirmed_cases": "sum", "deaths": "sum"})
    .reset_index()
)

In [13]:
county_df.head()

date        county  confirmed_cases  deaths
0 2020-01-26       Alameda                0     0.0
1 2020-01-26     Calaveras                0     0.0
2 2020-01-26  Contra Costa                0     0.0
3 2020-01-26      Humboldt                0     0.0
4 2020-01-26   Los Angeles                1     0.0

In [14]:
county_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5948 entries, 0 to 5947
Data columns (total 4 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             5948 non-null   datetime64[ns]
 1   county           5948 non-null   object        
 2   confirmed_cases  5948 non-null   int64         
 3   deaths           5948 non-null   float64       
dtypes: datetime64[ns](1), float64(1), int64(1), object(1)
memory usage: 186.0+ KB


## Chart the statewide totals over time

In [15]:
# Create a base chart with the common x-axis
chart = alt.Chart(state_df).encode(x=alt.X("date:T", title=None))

# Create the cases line
cases = chart.mark_line(color=lat.palette["default"]).encode(
    y=alt.Y("confirmed_cases:Q", title="Confirmed cases")
)

# Create the deaths line
deaths = chart.mark_line(color=lat.palette["schemes"]["ice-7"][3]).encode(
    y=alt.Y("deaths:Q", title="Deaths")
)

# Combine them into a single chart
(cases & deaths).properties(title="Statewide cumulative totals")

alt.VConcatChart(...)

## Chart the county totals

First on a linear scale

In [16]:
# Create the base chart
chart = (
    alt.Chart(county_df)
    .mark_line()
    .encode(
        x=alt.X("date:T", title=None),
        color=alt.Color("county:N", title="County", legend=None),
    )
)

# The cases line
cases = chart.encode(y=alt.Y("confirmed_cases:Q", title="Confirmed cases"),)

# The deaths line
deaths = chart.mark_line().encode(y=alt.Y("deaths:Q", title="Deaths"),)

# Combined into a chart
(cases & deaths).properties(title="Cumulative totals by county")

alt.VConcatChart(...)

Again on a logarithmic scale

In [17]:
# Make a base chart
chart = (
    alt.Chart(county_df)
    .mark_line()
    .encode(
        x=alt.X("date:T", title=None),
        color=alt.Color("county:N", title="County", legend=None),
    )
)

# The cases lines
cases = chart.transform_filter(alt.datum.confirmed_cases > 0).encode(
    y=alt.Y("confirmed_cases:Q", scale=alt.Scale(type="log"), title="Confirmed cases"),
)

# The deaths lines
deaths = chart.transform_filter(alt.datum.deaths > 0).encode(
    y=alt.Y("deaths:Q", scale=alt.Scale(type="log"), title="Deaths"),
)

# Slapping them together
(cases & deaths).properties(title="Cumulative totals by county")

alt.VConcatChart(...)

A common technique for clarifying these charts to begin each line on the day the county hit a minimum number. Let's try it with 10.

In [18]:
day_10_df = (
    county_df[
        # Filter down to only days with 10 or more cumulative cases
        county_df.confirmed_cases
        >= 10
    ]
    .groupby(
        # And then get the minimum date for each county
        "county"
    )
    .date.min()
    .reset_index()
)

Merge that date to each row in the data.

In [19]:
county_date_diff_df = county_df.merge(
    day_10_df, how="inner", on="county", suffixes=["", "_gte_10_cases"]
)

Calculate each day's distance from its tenth day.

In [20]:
county_date_diff_df["days_since_10"] = (
    county_date_diff_df.date - county_date_diff_df.date_gte_10_cases
).dt.days

Chart it.

In [21]:
alt.Chart(county_date_diff_df).transform_filter(
    # Only keep everything once they hit 10 cases
    alt.datum.days_since_10
    >= 0
).mark_line().encode(
    x=alt.X("days_since_10:O", title="Days since 10th case"),
    y=alt.Y("confirmed_cases:Q", scale=alt.Scale(type="log"), title="Confirmed cases"),
    color=alt.Color("county:N", title="County", legend=None),
).properties(
    title="Cumulative totals by county"
)

alt.Chart(...)

## County trends on a linear 'Pez' plot

Fill in any date gaps so that every county has a row for every date.

In [22]:
backfilled_county_df = (
    county_df.set_index(["county", "date"])
    .unstack("county")
    .fillna(0)
    .stack("county")
    .reset_index()
)

Calculate the rolling change in each county.

In [23]:
chronological_county_df = backfilled_county_df.sort_values(["county", "date"])

Calculate the daily change in each county.

In [24]:
chronological_county_df["new_confirmed_cases"] = chronological_county_df.groupby(
    "county"
).confirmed_cases.diff()

Let's chill that out as a seven-day average.

In [25]:
chronological_county_df["new_confirmed_cases_rolling_average"] = (
    chronological_county_df.groupby("county")
    .new_confirmed_cases.rolling(7)
    .mean()
    .droplevel(0)
)

Make the chart.

In [26]:
alt.Chart(chronological_county_df, title="New cases by day").mark_rect(
    stroke=None
).encode(
    x=alt.X(
        "date:O", axis=alt.Axis(ticks=False, grid=False, labels=False,), title=None
    ),
    y=alt.Y(
        "county:N",
        title="County",
        axis=alt.Axis(ticks=False, grid=False, labelPadding=5),
    ),
    color=alt.Color(
        "new_confirmed_cases_rolling_average:Q",
        scale=alt.Scale(
            type="threshold", domain=[0, 3, 10, 25, 50, 100, 500], scheme="blues"
        ),
        title="New cases (7-day average)",
    ),
).properties(
    height=800
)

alt.Chart(...)

## Chart new cases and deaths

Calculate the number of new cases each day using panda's [diff](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.diff.html) method.

In [27]:
state_df["new_confirmed_cases"] = state_df.confirmed_cases.diff()

Do the same for deaths

In [28]:
state_df["new_deaths"] = state_df.deaths.diff()

Now calculate the moving seven-day average of each using panda's [rolling](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.rolling.html) method.

In [29]:
state_df["new_confirmed_cases_rolling_average"] = state_df.new_confirmed_cases.rolling(
    7
).mean()

In [30]:
state_df["new_deaths_rolling_average"] = state_df.new_deaths.rolling(7).mean()

Put it all together on the chart 

In [31]:
# One base chart object with the data they all share
chart = alt.Chart(state_df).encode(x=alt.X("date:T", title=None),)

# The new cases bars
cases_bars = chart.mark_bar(color=lat.palette["default"]).encode(
    y=alt.Y("new_confirmed_cases:Q", title="New confirmed cases")
)

# The cases rolling average
cases_line = chart.mark_line(color=lat.palette["accent"]).encode(
    y=alt.Y("new_confirmed_cases_rolling_average:Q", title="7-day average")
)

# The new deaths bars
deaths_bars = chart.mark_bar(color=lat.palette["schemes"]["ice-7"][3]).encode(
    y=alt.Y("new_deaths:Q", title="New deaths")
)

# The deaths rolling average
deaths_line = chart.mark_line(color=lat.palette["schemes"]["ice-7"][6]).encode(
    y=alt.Y("new_deaths_rolling_average:Q", title="7-day average")
)

# Combine it all together into one paired chart
((cases_bars + cases_line) & (deaths_bars + deaths_line)).properties(
    title="New case and deaths statewide by day"
)

alt.VConcatChart(...)

Now do it by county

In [32]:
chronological_county_df.head()

date   county  confirmed_cases  deaths  new_confirmed_cases  \
0   2020-01-26  Alameda              0.0     0.0                  NaN   
58  2020-01-27  Alameda              0.0     0.0                  0.0   
116 2020-01-28  Alameda              0.0     0.0                  0.0   
174 2020-01-29  Alameda              0.0     0.0                  0.0   
232 2020-01-30  Alameda              0.0     0.0                  0.0   

     new_confirmed_cases_rolling_average  
0                                    NaN  
58                                   NaN  
116                                  NaN  
174                                  NaN  
232                                  NaN

Try it by county

In [33]:
alt.Chart(chronological_county_df, title="New cases by day").mark_line().encode(
    x=alt.X("date:O", axis=alt.Axis(ticks=False, grid=False, labels=False), title=None),
    y=alt.Y("new_confirmed_cases_rolling_average:Q", title="7-day average"),
    color=alt.Color("county:N", title="County", legend=None),
)

alt.Chart(...)

Create a statistic to measure recent changes in new cases

In [37]:
chronological_county_df.tail(14)

date county  confirmed_cases  deaths  new_confirmed_cases  \
7829 2020-06-08   Yuba             32.0     1.0                  0.0   
7887 2020-06-09   Yuba             32.0     1.0                  0.0   
7945 2020-06-10   Yuba             33.0     1.0                  1.0   
8003 2020-06-11   Yuba             34.0     1.0                  1.0   
8061 2020-06-12   Yuba             35.0     1.0                  1.0   
8119 2020-06-13   Yuba             35.0     1.0                  0.0   
8177 2020-06-14   Yuba             35.0     1.0                  0.0   
8235 2020-06-15   Yuba             36.0     1.0                  1.0   
8293 2020-06-16   Yuba             37.0     1.0                  1.0   
8351 2020-06-17   Yuba             39.0     1.0                  2.0   
8409 2020-06-18   Yuba             39.0     1.0                  0.0   
8467 2020-06-19   Yuba             41.0     1.0                  2.0   
8525 2020-06-20   Yuba             42.0     1.0                  1.0   
8583 2020-06-21   Yuba             42.0     1.0                  0.0   

      new_confirmed_cases_rolling_average  
7829                             0.285714  
7887                             0.142857  
7945                             0.285714  
8003                             0.428571  
8061                             0.428571  
8119                             0.428571  
8177                             0.428571  
8235                             0.571429  
8293                             0.714286  
8351                             0.857143  
8409                             0.714286  
8467                             0.857143  
8525                             1.000000  
8583                             1.000000

In [48]:
chronological_county_df[
    "new_confirmed_cases_rolling_average_two_week_pct_change"
] = chronological_county_df.groupby(
    "county"
).new_confirmed_cases_rolling_average.pct_change(
    14
)

In [53]:
latest_county_df = chronological_county_df[
    chronological_county_df.date == chronological_county_df.date.max()
]

In [66]:
biggest_county_jumps = latest_county_df[
    latest_county_df.new_confirmed_cases_rolling_average >= 25
].sort_values(
    "new_confirmed_cases_rolling_average_two_week_pct_change", ascending=False
)

In [75]:
def facet_wrap(subplts, plots_per_row):
    rows = [
        subplts[i : i + plots_per_row] for i in range(0, len(subplts), plots_per_row)
    ]
    compound_chart = alt.hconcat()
    for r in rows:
        rowplot = alt.vconcat()  # start a new row
        for item in r:
            rowplot |= item  # add suplot to current row as a new column
        compound_chart &= rowplot  # add the entire row of plots as a new row
    return compound_chart

In [111]:
chart_list = []
for county in list(biggest_county_jumps.head(12).county):
    this_df = chronological_county_df[chronological_county_df.county == county]
    chart = alt.Chart(this_df, title=county).encode(
        x=alt.X("date:T", title=None, axis=None),
    )
    lines = chart.mark_line(color=lat.palette["accent"]).encode(
        y=alt.Y("new_confirmed_cases_rolling_average:Q", title=None,),
    )
    bars = chart.mark_bar(color=lat.palette["default"], opacity=0.33).encode(
        y=alt.Y("new_confirmed_cases:Q", title="New confirmed cases",),
    )
    chart_list.append((bars + lines).properties(height=200, width=250))
facet_wrap(chart_list, plots_per_row=4)

alt.VConcatChart(...)

In [112]:
chart_list = []
for county in list(biggest_county_jumps.tail(12).county):
    this_df = chronological_county_df[chronological_county_df.county == county]
    chart = alt.Chart(this_df, title=county).encode(
        x=alt.X("date:T", title=None, axis=None),
    )
    lines = chart.mark_line(color=lat.palette["accent"]).encode(
        y=alt.Y("new_confirmed_cases_rolling_average:Q", title=None,),
    )
    bars = chart.mark_bar(color=lat.palette["default"], opacity=0.33).encode(
        y=alt.Y("new_confirmed_cases:Q", title="New confirmed cases",),
    )
    chart_list.append((bars + lines).properties(height=200, width=250))
facet_wrap(chart_list, plots_per_row=4)

alt.VConcatChart(...)

In [114]:
biggest_county_jumps.new_confirmed_cases_rolling_average_two_week_pct_change.describe()

count    22.000000
mean      0.997674
std       0.959813
min      -0.311563
25%       0.362187
50%       0.772164
75%       1.450797
max       3.142857
Name: new_confirmed_cases_rolling_average_two_week_pct_change, dtype: float64

In [115]:
biggest_county_jumps[
    biggest_county_jumps.new_confirmed_cases_rolling_average_two_week_pct_change < 0
]

date    county  confirmed_cases  deaths  new_confirmed_cases  \
8541 2020-06-21     Kings           2104.0    16.0                 13.0   
8538 2020-06-21  Imperial           4800.0    64.0                  0.0   

      new_confirmed_cases_rolling_average  \
8541                            42.714286   
8538                            91.857143   

      new_confirmed_cases_rolling_average_two_week_pct_change  
8541                                          -0.281250        
8538                                          -0.311563